In [1]:
import pandas as pd
import numpy as np
import holoviews as hv
import hvplot
import hvplot.pandas

In [8]:
df = pd.read_csv('./data/20210218-fridges-water-heater-v3.csv',
                 index_col='time',
                 parse_dates=True)

In [9]:
df.drop(columns='#',inplace=True)
df.head()

well_pump  new_fridge  water_heater  old_fridge
time                                                                
2021-02-11 12:54:36      0.037       0.501         0.147       0.684
2021-02-11 12:55:36      0.037       0.501         0.122       0.684
2021-02-11 12:56:36      0.037       0.501         0.147       0.684
2021-02-11 12:57:36      0.073       0.501         0.098       0.684
2021-02-11 12:58:36      0.049       0.501         0.122       0.684

In [10]:
# Account for the 220V appliances that were measured off of only one side:
df.well_pump = df.well_pump / 2
df.water_heater = df.water_heater / 2
df.head()

well_pump  new_fridge  water_heater  old_fridge
time                                                                
2021-02-11 12:54:36     0.0185       0.501        0.0735       0.684
2021-02-11 12:55:36     0.0185       0.501        0.0610       0.684
2021-02-11 12:56:36     0.0185       0.501        0.0735       0.684
2021-02-11 12:57:36     0.0365       0.501        0.0490       0.684
2021-02-11 12:58:36     0.0245       0.501        0.0610       0.684

In [11]:
# Start the data at xxxx once we know the data readers were in place
# df = df[df.index.values > pd.to_datetime('2021/02/10-4:30pm')]
df.hvplot.line()

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [12]:
staycation_start_line = hv.VLine(pd.to_datetime('2/12/2021-1pm'))
staycation_end_line = hv.VLine(pd.to_datetime('2/14/2021-1pm'))
staycation_start_line.opts(color='black', line_dash='dashed', line_width=1)    
staycation_end_line.opts(color='black', line_dash='dashed', line_width=1)    

df.drop(['water_heater','well_pump'],axis=1).hvplot.line() * staycation_start_line * staycation_end_line

:Overlay
   .NdOverlay.I :NdOverlay   [Variable]
      :Curve   [time]   (value)
   .VLine.I     :VLine   [x,y]
   .VLine.II    :VLine   [x,y]

In [13]:
df.drop(['new_fridge','old_fridge'],axis=1).hvplot.line() * staycation_start_line * staycation_end_line

:Overlay
   .NdOverlay.I :NdOverlay   [Variable]
      :Curve   [time]   (value)
   .VLine.I     :VLine   [x,y]
   .VLine.II    :VLine   [x,y]

In [14]:
# Convert to Whr's used
samples_per_hour = 60
fridge_voltage = 110
water_heater_voltage = 220
well_pump_voltage = 220



df['new_fridge_wh'] =   (df['new_fridge'] / samples_per_hour) * fridge_voltage
df['old_fridge_wh'] =   (df['old_fridge'] / samples_per_hour) * fridge_voltage
df['water_heater_wh'] = (df['water_heater'] / samples_per_hour) * water_heater_voltage
df['well_pump_wh'] = (df['well_pump'] / samples_per_hour) * well_pump_voltage

In [15]:

df['new_fridge_wh_accum'] =   df['new_fridge_wh'].cumsum()
df['old_fridge_wh_accum'] =   df['old_fridge_wh'].cumsum()
df['water_heater_wh_accum'] = df['water_heater_wh'].cumsum()
df['well_pump_wh_accum'] = df['well_pump_wh'].cumsum()



In [16]:
def plot_power_and_energy(df, scaling_factor=1):
    df['new_fridge_wh_accum'] =   df['new_fridge_wh_accum'] / scaling_factor
    df['old_fridge_wh_accum'] =   df['old_fridge_wh_accum'] / scaling_factor
    df['water_heater_wh_accum'] = df['water_heater_wh_accum'] / scaling_factor
    df['well_pump_wh_accum'] =    df['well_pump_wh_accum'] / scaling_factor
    
    plot = df.drop(['water_heater_wh_accum',
                    'water_heater_wh',
                   'well_pump_wh_accum',
                   'well_pump_wh'],axis=1).hvplot.line(width=900) * staycation_start_line * staycation_end_line
    
    df['new_fridge_wh_accum'] =   df['new_fridge_wh_accum'] * scaling_factor
    df['old_fridge_wh_accum'] =   df['old_fridge_wh_accum'] * scaling_factor
    df['water_heater_wh_accum'] = df['water_heater_wh_accum'] / scaling_factor
    df['well_pump_wh_accum'] =    df['well_pump_wh_accum'] * scaling_factor
    
    return plot

In [17]:
plot_power_and_energy(df.drop(['new_fridge',
                               'water_heater',
                               'old_fridge',
                               'well_pump'],axis=1),500) 

:Overlay
   .NdOverlay.I :NdOverlay   [Variable]
      :Curve   [time]   (value)
   .VLine.I     :VLine   [x,y]
   .VLine.II    :VLine   [x,y]

In [18]:
df_accum = df[['well_pump_wh_accum','water_heater_wh_accum','old_fridge_wh_accum','new_fridge_wh_accum']].copy()

In [19]:
df_accum

well_pump_wh_accum  water_heater_wh_accum  \
time                                                             
2021-02-11 12:54:36            0.067833               0.269500   
2021-02-11 12:55:36            0.135667               0.493167   
2021-02-11 12:56:36            0.203500               0.762667   
2021-02-11 12:57:36            0.337333               0.942333   
2021-02-11 12:58:36            0.427167               1.166000   
...                                 ...                    ...   
2021-02-18 13:38:36         2178.573833           55224.656667   
2021-02-18 13:39:36         2178.775500           55224.880333   
2021-02-18 13:40:36         2178.977167           55225.060000   
2021-02-18 13:41:36         2179.133000           55225.239667   
2021-02-18 13:42:36         2179.244833           55225.597167   

                     old_fridge_wh_accum  new_fridge_wh_accum  
time                                                           
2021-02-11 12:54:36             1.254000             0.918500  
2021-02-11 12:55:36             2.508000             1.837000  
2021-02-11 12:56:36             3.762000             2.755500  
2021-02-11 12:57:36             5.016000             3.674000  
2021-02-11 12:58:36             6.270000             4.592500  
...                                  ...                  ...  
2021-02-18 13:38:36          6573.523000         13559.463500  
2021-02-18 13:39:36          6573.792500         13560.493833  
2021-02-18 13:40:36          6573.972167         13561.524167  
2021-02-18 13:41:36          6574.195833         13562.530667  
2021-02-18 13:42:36          6574.239833         13563.537167  

[10129 rows x 4 columns]

In [20]:
df_accum.hvplot.line(grid=True)

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [21]:
df_orig = df[['well_pump_wh', 'water_heater_wh','old_fridge_wh','new_fridge_wh']]

In [22]:

df_orig_by_day = df_orig.resample('D').sum()
df_orig_by_day = df_orig_by_day[:-1]
df_orig_by_day = df_orig_by_day[1:]

In [23]:
df_orig_by_day.hvplot.line(grid=True)

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [24]:
# around 9 kWh / day for water heater

In [25]:
df_orig_by_day[2:].water_heater_wh.mean()

8930.368333333448